In [69]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset

import numpy as np

import matplotlib.pyplot as plt

import pandas as pd

In [70]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cpu')

In [71]:
train_data = pd.read_csv('train.csv')
test_data = pd.read_csv('test.csv')
valid_data = pd.read_csv('valid.csv')

In [72]:
data = pd.concat([train_data, test_data, valid_data], join='inner')
data

questions   
0     Can you imagine the world without internet acc...  \
1     Can you imagine the world without internet acc...   
2     Can you imagine the world without internet acc...   
3     Can you imagine the world without internet acc...   
4     I am just finishing my university course and I...   
...                                                 ...   
3412  Hi, I'm looking to buy a Harley bike. Have you...   
3413  My sister is a baker. She bakes mostly cakes a...   
3414  My sister is a baker. She bakes mostly cakes a...   
3415  My sister is a baker. She bakes mostly cakes a...   
3416  My sister is a baker. She bakes mostly cakes a...   

                                                answers  
0     Yeah, but once the access to the internet was ...  
1     Well, I know that more people started using it...  
2     Yeah. And the Internet actually developed from...  
3     Well, I know that it is defined as the ability...  
4     I am a bot so that is not posible. Do you perf...  
...                                                 ...  
3412       I do, it was founded in Milwaukee, Wisconsin  
3413                      A baker is someone who bakes.  
3414  It has to do with breads and other products ma...  
3415  That's great! Baking has been around as long a...  
3416  So, in farming the quality of the grain depend...  

[25313 rows x 2 columns]

In [73]:
question_train = data['questions']
answer_train = data['answers']
question_test = data['questions'][-100:]
answer_test = data['answers'][-100:]


In [76]:
question_train = [sent.strip().split(" ") for sent in question_train] 
question_test = [sent.strip().split(" ") for sent in question_test]
answer_train = [sent.strip().split(" ") for sent in answer_train]
answer_test = [sent.strip().split(" ") for sent in answer_test]

In [77]:
ques_index2word = ["<PAD>", "<SOS>", "<EOS>"]
ans_index2word = ["<PAD>", "<SOS>", "<EOS>"]

for ds in [question_train, question_test]:
    for sent in ds:
        for token in sent:
            if token not in ques_index2word:
                ques_index2word.append(token)

for ds in [answer_train, answer_test]:
    for sent in ds:
        for token in sent:
            if token not in ans_index2word:
                ans_index2word.append(token)

In [78]:
ques_word2index = {token: idx for idx, token in enumerate(ques_index2word)}
ans_word2index = {token: idx for idx, token in enumerate(ans_index2word)}

In [79]:
ques_index2word[20]

'do'

In [80]:
ques_word2index["do"]

20

In [81]:
ques_lenghts = sum([len(sent) for sent in question_train])/len(question_train)
ans_lengths = sum([len(sent) for sent in answer_train])/len(answer_train)

In [82]:
ques_lenghts

69.53624619760598

In [83]:
ans_lengths

17.424603958440326

In [84]:
seq_length = 200

In [85]:
def encode_and_pad(vocab, sent, max_length):
    sos = [vocab["<SOS>"]]
    eos = [vocab["<EOS>"]]
    pad = [vocab["<PAD>"]]

    if len(sent) < max_length - 2: 
        n_pads = max_length - 2 - len(sent)
        encoded = [vocab[w] for w in sent]
        return sos + encoded + eos + pad * n_pads 
    else:
        encoded = [vocab[w] for w in sent]
        truncated = encoded[: max_length-2]
        return sos + truncated + eos

In [86]:
ques_train_encoded = [encode_and_pad(ques_word2index, sent, seq_length) for sent in question_train]
ques_test_encoded = [encode_and_pad(ques_word2index, sent, seq_length) for sent in question_test]
ans_train_encoded = [encode_and_pad(ans_word2index, sent, seq_length) for sent in answer_train]
ans_test_encoded = [encode_and_pad(ans_word2index, sent, seq_length) for sent in answer_test]

In [87]:
batch_size = 60

train_x = np.array(ques_train_encoded)
train_y = np.array(ans_train_encoded)
test_x = np.array(ques_test_encoded)
test_y = np.array(ans_test_encoded)

train_ds = TensorDataset(torch.from_numpy(train_x), torch.from_numpy(train_y))
test_ds = TensorDataset(torch.from_numpy(test_x), torch.from_numpy(test_y))


train_dl = DataLoader(train_ds, shuffle=True, batch_size=batch_size, drop_last=True)
test_dl = DataLoader(test_ds, shuffle=True, batch_size=batch_size, drop_last=True)

In [29]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size, padding_idx=0)
        
        self.gru = nn.GRU(hidden_size, hidden_size, batch_first=True)

    def forward(self, input, hidden):
        embedded = self.embedding(input)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, batch_size, self.hidden_size)

In [30]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size, padding_idx=0)
        
        self.gru = nn.GRU(hidden_size, hidden_size)

        self.out = nn.Linear(hidden_size, output_size)

        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input)

        output = F.relu(output)

        output, hidden = self.gru(output, hidden)

        output = self.softmax(self.out(output[0]))
        
        return output, hidden

In [31]:
hidden_size = 128

In [32]:
encoder = EncoderRNN(len(ques_index2word), hidden_size).to(device)
decoder = DecoderRNN(hidden_size, len(ans_index2word)).to(device)

In [33]:
encoder

EncoderRNN(
  (embedding): Embedding(48073, 128, padding_idx=0)
  (gru): GRU(128, 128, batch_first=True)
)

In [34]:
decoder

DecoderRNN(
  (embedding): Embedding(39653, 128, padding_idx=0)
  (gru): GRU(128, 128)
  (out): Linear(in_features=128, out_features=39653, bias=True)
  (softmax): LogSoftmax(dim=1)
)

In [35]:
criterion = nn.CrossEntropyLoss()
enc_optimizer = torch.optim.Adam(encoder.parameters(), lr = 3e-3)
dec_optimizer = torch.optim.Adam(decoder.parameters(), lr = 3e-3)

In [36]:
losses = []


In [37]:
input_length = target_length = seq_length

SOS = ques_word2index["<SOS>"]
EOS = ques_word2index["<EOS>"]

epochs = 15

for epoch in range(epochs):
    for idx, batch in enumerate(train_dl):

        print(idx,batch, '-->', epoch)

        encoder_hidden = encoder.initHidden()

        encoder_hidden = encoder_hidden.to(device)

        input_tensor = batch[0].to(device)

        target_tensor = batch[1].to(device)
        

        enc_optimizer.zero_grad()
        dec_optimizer.zero_grad()

        with torch.set_grad_enabled(True):
            
            encoder_output, encoder_hidden = encoder(input_tensor, encoder_hidden)

            dec_result = torch.zeros(target_length, batch_size, len(ans_index2word)).to(device)

            decoder_input = target_tensor[:, 0].unsqueeze(dim=0).to(device)

            decoder_hidden = encoder_hidden

            for i in range(1, target_length):
                
                decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden)
                
                best = decoder_output.argmax(1)

                decoder_input = best.unsqueeze(dim=0) 

                dec_result[i] = decoder_output


            scores = dec_result.transpose(1, 0)[1:].reshape(-1, dec_result.shape[2])
            targets = target_tensor[1:].reshape(-1)

            loss = criterion(scores, targets)
            
            loss.backward()
            
            torch.nn.utils.clip_grad_norm_(encoder.parameters(), max_norm=1)
            torch.nn.utils.clip_grad_norm_(decoder.parameters(), max_norm=1)

            enc_optimizer.step()
            dec_optimizer.step()

            losses.append(loss.item())
            print(idx, sum(losses)/len(losses))

0 [tensor([[    1,    22,   489,  ...,     0,     0,     0],
        [    1,   248,  2879,  ...,     0,     0,     0],
        [    1,  5781,   534,  ...,     0,     0,     0],
        ...,
        [    1,   104,     4,  ...,     0,     0,     0],
        [    1,  1028,   210,  ...,     0,     0,     0],
        [    1, 42985,  1250,  ...,     0,     0,     0]]), tensor([[    1,   596,   130,  ...,     0,     0,     0],
        [    1,    18,   602,  ...,     0,     0,     0],
        [    1,   141,   334,  ...,     0,     0,     0],
        ...,
        [    1, 14076,  3396,  ...,     0,     0,     0],
        [    1, 19494,   156,  ...,     0,     0,     0],
        [    1,    17,   856,  ...,     0,     0,     0]])] --> 0
0 10.749817848205566
1 [tensor([[   1,   22, 5665,  ...,    0,    0,    0],
        [   1,   22,  162,  ...,    0,    0,    0],
        [   1, 3406,  121,  ...,    0,    0,    0],
        ...,
        [   1,  209,    4,  ...,    0,    0,    0],
        [   1,   22,

In [38]:
plt.plot(losses)


In [39]:
test_sentence = "I love candy, what's a good brand?	"

test_sentence = torch.tensor(encode_and_pad(ques_word2index, test_sentence.split(), seq_length)).unsqueeze(dim=0)

In [48]:
encoder_hidden = torch.zeros(1, 1, hidden_size)
encoder_hidden = encoder_hidden.to(device)

input_tensor = test_sentence.to(device)

enc_optimizer.zero_grad()
dec_optimizer.zero_grad()

result = []

encoder_outputs = torch.zeros(seq_length, encoder.hidden_size, device=device)


with torch.set_grad_enabled(False):
    encoder_output, encoder_hidden = encoder(input_tensor, encoder_hidden)

    dec_result = torch.zeros(target_length, 1, len(ans_index2word)).to(device)

    decoder_input = torch.tensor([SOS]).unsqueeze(dim=0).to(device)
    decoder_hidden = encoder_hidden
    for di in range(1, target_length):
        decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden)
        best = decoder_output.argmax(1)
        result.append(ans_index2word[best.to('cpu').item()])
        if best.item() == EOS:
            break

        decoder_input = best.unsqueeze(dim=0) 
        dec_result[di] = decoder_output

    scores = dec_result.reshape(-1, dec_result.shape[2])
    targets = target_tensor.reshape(-1)

In [49]:
" ".join(result)


"I I you you know know a a the Dylan's Dylan's Bar a Bar a the the the <EOS>"

In [43]:
torch.save(encoder.state_dict(), './encoder')
torch.save(decoder.state_dict(), './decoder')

In [44]:
model_encoder = EncoderRNN(len(ques_index2word), hidden_size).to(device)
model_encoder.load_state_dict(torch.load('./encoder'))
model_encoder.eval()

EncoderRNN(
  (embedding): Embedding(48073, 128, padding_idx=0)
  (gru): GRU(128, 128, batch_first=True)
)

In [45]:
model_decoder = DecoderRNN(hidden_size, len(ans_index2word)).to(device)
model_decoder.load_state_dict(torch.load('./decoder'))
model_decoder.eval()

DecoderRNN(
  (embedding): Embedding(39653, 128, padding_idx=0)
  (gru): GRU(128, 128)
  (out): Linear(in_features=128, out_features=39653, bias=True)
  (softmax): LogSoftmax(dim=1)
)

In [52]:
encoder_hidden = torch.zeros(1, 1, hidden_size)
encoder_hidden = encoder_hidden.to(device)

input_tensor = test_sentence.to(device)

enc_optimizer.zero_grad()
dec_optimizer.zero_grad()

result = []

encoder_outputs = torch.zeros(seq_length, model_encoder.hidden_size, device=device)


with torch.set_grad_enabled(False):
    encoder_output, encoder_hidden = model_encoder(input_tensor, encoder_hidden)

    dec_result = torch.zeros(target_length, 1, len(ans_index2word)).to(device)

    decoder_input = torch.tensor([SOS]).unsqueeze(dim=0).to(device)
    decoder_hidden = encoder_hidden
    for di in range(1, target_length):
        decoder_output, decoder_hidden = model_decoder(decoder_input, decoder_hidden)
        best = decoder_output.argmax(1)
        result.append(ans_index2word[best.to('cpu').item()])
        if best.item() == EOS:
            break

        decoder_input = best.unsqueeze(dim=0) 
        dec_result[di] = decoder_output

    scores = dec_result.reshape(-1, dec_result.shape[2])
    targets = target_tensor.reshape(-1)

In [53]:
" ".join(result)

"I I you you know know a a the Dylan's Dylan's Bar a Bar a the the the <EOS>"

In [54]:
len(ans_index2word)

39653

In [64]:
indices = [{'ans_w2i': ans_word2index, 'ques_i2w': ques_index2word, 'ans_i2w': ans_index2word, 'ques_w2i': ques_word2index}]

In [65]:
import json
f = open('./indices.json', 'w')
json.dump(indices, f, indent=6)